# AGN Type I Catalogue

**A Comprehensive and Uniform Sample of Broad-line Active Galactic Nuclei from the SDSS DR7**

https://iopscience.iop.org/article/10.3847/1538-4365/ab298b

In [1]:
from astropy.io import fits
from astropy.table import Table
from matplotlib import pyplot as plt
from astroML.datasets import fetch_sdss_spectrum
import multiprocessing
import pandas as pd
from functools import partial
import numpy as np
import glob
import re

# Read fits file

In [2]:
## file containing the basic infotmation of all Type I AGNs
typeIList = Table.read('typeIList.fits', format='fits').to_pandas()

## file containing the fittings all Type I AGNs
typeIFitting = Table.read('typeIFitting.fits', format='fits').to_pandas()

## file containing all galaxies
galaxy = Table.read('sdss_dr7_catalog_galaxies.fits', format='fits').to_pandas()

## file containing all QSOs
QSO = Table.read('sdss_dr7_catalog_qso.fits', format='fits').to_pandas()

In [4]:
typeI = typeIList.merge(typeIFitting, right_on=['ID'],left_on=['ID'], how='inner')
galaxyTypeI = galaxy.merge(typeI, right_on=['RA','DEC','Z','PLATE','MJD','FIBERID'],left_on=['RA','DEC','Z','PLATE','MJD','FIBERID'], how='inner')
QSOTypeI = QSO.merge(typeI, right_on=['RA','DEC','Z','PLATE','MJD','FIBERID'],left_on=['RA','DEC','Z','PLATE','MJD','FIBERID'], how='inner')

In [6]:
galaxyTypeI[:5]

RA       DEC  PLATE    MJD  FIBERID         Z  SPECCLASS      ZERR  \
0  146.88330 -0.494699    266  51630       70  0.083761          2  0.000115   
1  148.35708 -1.061524    267  51608       84  0.083748          2  0.000217   
2  150.44875 -0.385375    268  51633       21  0.090303          2  0.000144   
3  149.65000 -0.995160    268  51633       85  0.167000          2  0.000935   
4  149.10248 -0.937019    268  51633      206  0.091056          2  0.000167   

     ID             DESIGNATION     ...      LFEII4570_ERR  EW_FEII4570  \
0  3495  b'J094731.99-002940.9'     ...             -999.0       -999.0   
1  3641  b'J095325.70-010341.5'     ...             -999.0       -999.0   
2  3816  b'J100147.70-002307.4'     ...             -999.0       -999.0   
3  3735  b'J095836.00-005942.6'     ...             -999.0       -999.0   
4  3699  b'J095624.60-005613.3'     ...             -999.0       -999.0   

   EW_FEII4570_ERR      L5100  L5100_ERR  MULTI_PEAK   MBH_BHB   MBH_BHA  \
0           -999.0  43.166987   0.002160           0  8.004194  7.672554   
1           -999.0  43.351087   0.042986           0  8.308055  8.110505   
2           -999.0  43.771085   0.058191           0  7.500089  6.931945   
3           -999.0  43.569074   0.000937           0  6.738769  6.450302   
4           -999.0  43.831510   0.095558           0  8.468289  7.880238   

        MBH  LAMBDA_EDD  
0  7.869289   -2.624195  
1  8.220417   -2.571006  
2  7.302967   -1.794967  
3  6.618059   -0.813983  
4  8.267007   -2.782818  

[5 rows x 75 columns]

# Make sy19 and 20 lists

In [23]:
sy19_filenames = glob.glob('../Sy19_train/*.fits')+glob.glob('../Sy19_test/*.fits')
sy20_filenames = glob.glob('../Sy20_train/*.fits')+glob.glob('../Sy20_test/*.fits')

sy19_list = [re.findall(r'\d+', filename) for filename in sy19_filenames]
sy20_list = [re.findall(r'\d+', filename) for filename in sy20_filenames]

sy19 = pd.DataFrame(sy19_list, columns=["CLASS", "PLATE", "MJD", "FIBERID"], dtype='int')
sy20 = pd.DataFrame(sy20_list, columns=["CLASS", "PLATE", "MJD", "FIBERID"], dtype='int')

# Define multithreds functions

In [21]:
def parallelize_dataframe(df,func,data_home='./',number=8):
    num_partitions = number # number of partitions to split dataframe
    df_split = np.array_split(df, num_partitions)
    pool = multiprocessing.Pool(num_partitions)
    f = partial(func, data_home)
    pool.map(f, df_split)
    pool.close()
    pool.join()
    return

def download(data_home,df):
    # Fetch single spectrum
    for index, row in df.iterrows():
        try:
            fetch_sdss_spectrum(row['PLATE'], row['MJD'], row['FIBERID'], data_home=data_home)
        except:
            print("!!!!! Failed:",row['PLATE'], row['MJD'], row['FIBERID'])

# Download galaxy Type I

In [ ]:
parallelize_dataframe(galaxyTypeI,download,data_home='./galaxy',number=8)

# Download QSO Type I

In [ ]:
parallelize_dataframe(QSOTypeI,download,data_home='./QSO',number=8)

# Download sy19

In [24]:
parallelize_dataframe(sy19,download,data_home='./sy19',number=8)

[==================================     ]  155.4kb / 182.8kb    
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/0836/spSpec-52376-0836-562.fit
caching to ./sy19/SDSSspec/0619/spSpec-52056-0619-312.fit8kb   
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/1700/spSpec-53502-1700-497.fit.8kb   
[=======================================]  178.2kb / 182.8kb   
[====================================== ]  173.7kb / 182.8kb   
caching to ./sy19/SDSSspec/0558/spSpec-52317-0558-481.fit.8kb   

caching to ./sy19/SDSSspec/2587/spSpec-54138-2587-219.fit
caching to ./sy19/SDSSspec/1286/spSpec-52725-1286-013.fit
[========================================]  182.8kb / 182.8kb   

caching to ./sy19/SDSSspec/1618/spSpec-53116-1618-082.fit
caching to ./sy19/SDSSspec/0710/spSpec-52203-0710-483.fit
[=======================                ]  105.1kb / 182.8kb    
caching to ./sy19/SDSSspec/2005/spSpec-53472-2005-441.fit
[==

[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/2357/spSpec-53793-2357-160.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/0371/spSpec-52078-0371-269.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/0655/spSpec-52162-0655-315.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/0498/spSpec-51984-0498-037.fitkb   
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/2010/spSpec-53495-2010-255.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/1674/spSpec-53464-1674-082.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/1454/spSpec-53090-1454-467.fit
[========================================]  185.6kb / 185.6kb   
caching to ./sy19/SDSSspec/0390/spSpec-51900-0390-456.fit
[==========

[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/1333/spSpec-52782-1333-140.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/0816/spSpec-52379-0816-015.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/0340/spSpec-51990-0340-080.fitkb   
[========================================]  182.8kb / 182.8kb   

caching to ./sy19/SDSSspec/2127/spSpec-53859-2127-085.fitkb   
caching to ./sy19/SDSSspec/1974/spSpec-53430-1974-610.fitkb    
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/0947/spSpec-52411-0947-500.fitb   
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/0446/spSpec-51899-0446-394.fit
[=                                      ]  4.6kb / 182.8kb      
caching to ./sy19/SDSSspec/2143/spSpec-54184-2143-070.fitkb   
[========================================]  182.8kb / 1

[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/2118/spSpec-53820-2118-263.fitkb   
[========================================]  180.0kb / 180.0kb   
caching to ./sy19/SDSSspec/2435/spSpec-53828-2435-435.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/1040/spSpec-52722-1040-522.fit
[=======================                ]  105.1kb / 182.8kb    
caching to ./sy19/SDSSspec/1236/spSpec-52751-1236-198.fit8kb   
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/0892/spSpec-52378-0892-505.fitkb    
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/0606/spSpec-52365-0606-290.fit8kb   
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/1811/spSpec-53533-1811-299.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/2503/spSpec-53856-2503-5

[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/2528/spSpec-54571-2528-613.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/2162/spSpec-54207-2162-465.fit

caching to ./sy19/SDSSspec/1599/spSpec-53089-1599-469.fit8kb   
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/0606/spSpec-52365-0606-154.fit
[=======================                ]  105.1kb / 182.8kb    
caching to ./sy19/SDSSspec/1195/spSpec-52724-1195-391.fit8kb   
[====================================   ]  164.5kb / 182.8kb    
caching to ./sy19/SDSSspec/2419/spSpec-54139-2419-043.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/1983/spSpec-53442-1983-028.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/1589/spSpec-52972-1589-331.fit
[========================================]  182.8kb / 182.8kb   
cac

...

[=================                      ]  77.7kb / 182.8kb     
caching to ./sy19/SDSSspec/2593/spSpec-54175-2593-422.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/1736/spSpec-53052-1736-621.fit8kb   
[===========================            ]  123.4kb / 182.8kb    
caching to ./sy19/SDSSspec/0302/spSpec-51688-0302-148.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/2424/spSpec-54448-2424-584.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/0886/spSpec-52381-0886-455.fit
[====================================   ]  164.5kb / 182.8kb    
caching to ./sy19/SDSSspec/1811/spSpec-53533-1811-145.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/2110/spSpec-53467-2110-637.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/1443/spSpec-53055-1443-478.fit
[=========

[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/2605/spSpec-54484-2605-537.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/2150/spSpec-54510-2150-047.fit
[=====================                  ]  96.0kb / 182.8kb     
caching to ./sy19/SDSSspec/0554/spSpec-52000-0554-352.fit
[================================       ]  146.2kb / 182.8kb    
caching to ./sy19/SDSSspec/2745/spSpec-54231-2745-119.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/1814/spSpec-54555-1814-405.fit

caching to ./sy19/SDSSspec/2653/spSpec-54230-2653-180.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/0593/spSpec-52026-0593-498.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/2600/spSpec-54243-2600-340.fit
[======                                 ]  27.4kb / 182.8kb     
caching to ./sy

[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/0781/spSpec-52373-0781-248.fit
[============================           ]  129.9kb / 185.6kb    
caching to ./sy19/SDSSspec/0980/spSpec-52431-0980-238.fit8kb   
[========================================]  185.6kb / 185.6kb   
caching to ./sy19/SDSSspec/1820/spSpec-54208-1820-211.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/0503/spSpec-51999-0503-081.fit8kb   
[===============================        ]  141.7kb / 182.8kb    
caching to ./sy19/SDSSspec/0663/spSpec-52145-0663-342.fitkb    
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/0409/spSpec-51871-0409-087.fitkb   
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/0471/spSpec-51924-0471-578.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/1467/spSpec-53115-1467-5

[===============                        ]  68.6kb / 182.8kb     
caching to ./sy19/SDSSspec/2228/spSpec-53818-2228-631.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/1373/spSpec-53063-1373-471.fitkb    
[==========================             ]  118.8kb / 182.8kb   
caching to ./sy19/SDSSspec/0501/spSpec-52235-0501-366.fit8kb   
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/0409/spSpec-51871-0409-479.fit8kb   
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/1051/spSpec-52468-1051-119.fit
[====                                   ]  18.3kb / 182.8kb     
caching to ./sy19/SDSSspec/1024/spSpec-52826-1024-537.fitkb    
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/0434/spSpec-51885-0434-567.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/2507/spSpec-53876-2507-4

[=========================              ]  114.3kb / 182.8kb    
caching to ./sy19/SDSSspec/1576/spSpec-53496-1576-252.fit8kb   
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/2096/spSpec-53446-2096-020.fit8kb   
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/0481/spSpec-51908-0481-420.fit
[====================================== ]  173.7kb / 182.8kb    
caching to ./sy19/SDSSspec/2524/spSpec-54568-2524-589.fit.8kb   

caching to ./sy19/SDSSspec/0404/spSpec-51812-0404-343.fit
[==================================     ]  155.4kb / 182.8kb    
[========================================]  182.8kb / 182.8kb   
caching to ./sy19/SDSSspec/0462/spSpec-51909-0462-284.fit
caching to ./sy19/SDSSspec/1784/spSpec-54425-1784-455.fit
[===========================            ]  123.4kb / 182.8kb    
caching to ./sy19/SDSSspec/2765/spSpec-54535-2765-429.fit8kb   
[========================================]  182.8kb / 1

# Download sy20

In [ ]:
parallelize_dataframe(sy20,download,data_home='./sy20',number=25)

[=================================      ]  150.8kb / 182.8kb    
caching to ./sy20/SDSSspec/1786/spSpec-54450-1786-398.fit8kb    
[==================================     ]  155.4kb / 182.8kb   
caching to ./sy20/SDSSspec/0653/spSpec-52145-0653-170.fit8kb   
[==================================     ]  155.4kb / 182.8kb    
[====================================   ]  164.5kb / 182.8kb    
[=================================      ]  150.8kb / 182.8kb    
[====================================== ]  173.7kb / 182.8kb   
caching to ./sy20/SDSSspec/0613/spSpec-52345-0613-585.fit8kb   
caching to ./sy20/SDSSspec/2951/spSpec-54592-2951-229.fit8kb   
caching to ./sy20/SDSSspec/0829/spSpec-52296-0829-473.fit.8kb   
caching to ./sy20/SDSSspec/2597/spSpec-54231-2597-211.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy20/SDSSspec/1010/spSpec-52649-1010-101.fit8kb    
[====================================== ]  173.7kb / 182.8kb    

caching to ./sy20/SDSSspec/1875/spSp

[======================                 ]  100.5kb / 182.8kb    
caching to ./sy20/SDSSspec/0428/spSpec-51883-0428-208.fit8kb   
[=========                              ]  41.1kb / 182.8kb     
caching to ./sy20/SDSSspec/0695/spSpec-52202-0695-152.fit8kb   
[===========                            ]  50.3kb / 182.8kb     
caching to ./sy20/SDSSspec/1713/spSpec-53827-1713-268.fit8kb   
[=======================================]  178.2kb / 182.8kb    
[===============                        ]  68.6kb / 182.8kb     
caching to ./sy20/SDSSspec/0874/spSpec-52338-0874-594.fit
caching to ./sy20/SDSSspec/0610/spSpec-52056-0610-586.fitkb   
[=                                      ]  4.6kb / 182.8kb      
[=====================                  ]  96.0kb / 182.8kb     
caching to ./sy20/SDSSspec/1341/spSpec-52786-1341-212.fit8kb   
caching to ./sy20/SDSSspec/2137/spSpec-54206-2137-122.fit8kb   
[========================               ]  109.7kb / 182.8kb    
caching to ./sy20/SDSSspec/0490/spSpec-

[========================================]  182.8kb / 182.8kb   
caching to ./sy20/SDSSspec/0446/spSpec-51899-0446-266.fitkb   
[====                                   ]  18.3kb / 182.8kb     
caching to ./sy20/SDSSspec/1497/spSpec-52886-1497-433.fit
[=================                      ]  77.7kb / 182.8kb     
caching to ./sy20/SDSSspec/0737/spSpec-52518-0737-544.fitkb    
[=========                              ]  41.1kb / 182.8kb     
caching to ./sy20/SDSSspec/1969/spSpec-53383-1969-163.fit8kb   
[=                                      ]  4.6kb / 182.8kb     
caching to ./sy20/SDSSspec/2363/spSpec-53763-2363-248.fitkb     

caching to ./sy20/SDSSspec/0858/spSpec-52316-0858-557.fitkb    
[===============                        ]  68.6kb / 182.8kb     
caching to ./sy20/SDSSspec/1610/spSpec-53144-1610-447.fit8kb   
[===================================    ]  160.0kb / 182.8kb    
[=====================================  ]  169.1kb / 182.8kb   
caching to ./sy20/SDSSspec/0578/spSpec-

[=======================================]  178.2kb / 182.8kb    
[======                                 ]  27.4kb / 182.8kb   
caching to ./sy20/SDSSspec/1038/spSpec-52673-1038-028.fitkb   
caching to ./sy20/SDSSspec/1188/spSpec-52650-1188-493.fit
[=============                          ]  59.4kb / 182.8kb     
caching to ./sy20/SDSSspec/2784/spSpec-54529-2784-326.fitkb   
[====================                   ]  91.4kb / 182.8kb     
caching to ./sy20/SDSSspec/2532/spSpec-54589-2532-365.fitkb   
[========================================]  182.8kb / 182.8kb   
caching to ./sy20/SDSSspec/2881/spSpec-54502-2881-057.fit
[=====================                  ]  96.0kb / 182.8kb     
caching to ./sy20/SDSSspec/1714/spSpec-53521-1714-100.fitkb    
[=============                          ]  59.4kb / 182.8kb   
[================================       ]  146.2kb / 182.8kb   
caching to ./sy20/SDSSspec/2752/spSpec-54533-2752-615.fitkb    
caching to ./sy20/SDSSspec/0426/spSpec-51882-0426-07

[============================           ]  128.0kb / 182.8kb   
caching to ./sy20/SDSSspec/1495/spSpec-52944-1495-376.fit8kb   
caching to ./sy20/SDSSspec/1407/spSpec-52886-1407-236.fit8kb   

caching to ./sy20/SDSSspec/1818/spSpec-54539-1818-566.fit8kb   
[====                                   ]  18.3kb / 182.8kb     
caching to ./sy20/SDSSspec/0990/spSpec-52465-0990-560.fit8kb   
[=================================      ]  150.8kb / 182.8kb    
caching to ./sy20/SDSSspec/1798/spSpec-53851-1798-541.fitkb    
[========================================]  182.8kb / 182.8kb   
caching to ./sy20/SDSSspec/1799/spSpec-53556-1799-540.fit8kb   
[========================================]  182.8kb / 182.8kb   
caching to ./sy20/SDSSspec/2582/spSpec-54139-2582-445.fit8kb   
[=========================              ]  114.3kb / 182.8kb    
caching to ./sy20/SDSSspec/1813/spSpec-53903-1813-313.fit8kb   
[====================================== ]  173.7kb / 182.8kb    
caching to ./sy20/SDSSspec/0413/s

...

[=                                      ]  4.6kb / 182.8kb     
caching to ./sy20/SDSSspec/0682/spSpec-52525-0682-210.fitb     
[=================                      ]  77.7kb / 182.8kb     
caching to ./sy20/SDSSspec/0402/spSpec-51793-0402-065.fitkb   
[=============                          ]  59.4kb / 182.8kb     
caching to ./sy20/SDSSspec/1431/spSpec-52992-1431-565.fitkb   
[=======                                ]  32.0kb / 182.8kb     
caching to ./sy20/SDSSspec/0285/spSpec-51930-0285-416.fit8kb   
[========                               ]  36.6kb / 182.8kb     
caching to ./sy20/SDSSspec/1453/spSpec-53084-1453-417.fit8kb    
[============                           ]  55.7kb / 185.6kb     
[================                       ]  73.1kb / 182.8kb    
caching to ./sy20/SDSSspec/0678/spSpec-52884-0678-604.fit8kb   
caching to ./sy20/SDSSspec/0438/spSpec-51884-0438-252.fitkb    
[===================                    ]  86.8kb / 182.8kb     
[================                  

[===========================            ]  123.4kb / 182.8kb    
caching to ./sy20/SDSSspec/2012/spSpec-53493-2012-182.fit8kb   

caching to ./sy20/SDSSspec/1460/spSpec-53138-1460-092.fit8kb   
[====================================   ]  164.5kb / 182.8kb    
caching to ./sy20/SDSSspec/1793/spSpec-53883-1793-482.fit8kb   
[================================       ]  146.2kb / 182.8kb    
[=====================================  ]  169.1kb / 182.8kb   
[====================================== ]  173.7kb / 182.8kb   
caching to ./sy20/SDSSspec/0393/spSpec-51794-0393-501.fit
caching to ./sy20/SDSSspec/0747/spSpec-52234-0747-154.fit
caching to ./sy20/SDSSspec/2373/spSpec-53768-2373-393.fit8kb   
[====================================== ]  173.7kb / 182.8kb   
caching to ./sy20/SDSSspec/2645/spSpec-54477-2645-391.fit8kb   
[=======================================]  178.2kb / 182.8kb    
[=======================================]  178.2kb / 182.8kb    
[========================================]  18

[=======================                ]  105.1kb / 182.8kb    
caching to ./sy20/SDSSspec/1954/spSpec-53357-1954-283.fit8kb    
[=====================================  ]  169.1kb / 182.8kb   
caching to ./sy20/SDSSspec/1032/spSpec-53175-1032-236.fit8kb   
[========================================]  182.8kb / 182.8kb   
[=======================================]  178.2kb / 182.8kb   

caching to ./sy20/SDSSspec/0961/spSpec-52615-0961-038.fit8kb   
[=======================================]  178.2kb / 182.8kb   
caching to ./sy20/SDSSspec/1210/spSpec-52701-1210-162.fit8kb    
caching to ./sy20/SDSSspec/0615/spSpec-52347-0615-306.fit.8kb   
[================================       ]  146.2kb / 182.8kb   
[===================================    ]  160.0kb / 182.8kb   
caching to ./sy20/SDSSspec/1199/spSpec-52703-1199-040.fit
caching to ./sy20/SDSSspec/0938/spSpec-52708-0938-046.fit
caching to ./sy20/SDSSspec/1678/spSpec-53433-1678-450.fit.8kb   
[==========================             ]  11

[=====================================  ]  169.1kb / 182.8kb    
caching to ./sy20/SDSSspec/2103/spSpec-53467-2103-221.fit8kb   
[========================================]  182.8kb / 182.8kb   
caching to ./sy20/SDSSspec/2786/spSpec-54540-2786-063.fit
[==========                             ]  45.7kb / 182.8kb     
[====================================== ]  173.7kb / 182.8kb   
caching to ./sy20/SDSSspec/2096/spSpec-53446-2096-381.fit8kb   
caching to ./sy20/SDSSspec/0998/spSpec-52750-0998-078.fit
[========================================]  182.8kb / 182.8kb   
caching to ./sy20/SDSSspec/0802/spSpec-52289-0802-382.fit.8kb   

caching to ./sy20/SDSSspec/0513/spSpec-51989-0513-599.fitb   
[==================                     ]  82.3kb / 182.8kb     
caching to ./sy20/SDSSspec/1999/spSpec-53503-1999-485.fit8kb   
[==============                         ]  64.0kb / 182.8kb     
caching to ./sy20/SDSSspec/1421/spSpec-53149-1421-044.fit8kb   
[===============================        ]  141

[=====                                  ]  22.9kb / 182.8kb   
caching to ./sy20/SDSSspec/0802/spSpec-52289-0802-079.fitb    
[=================================      ]  150.8kb / 182.8kb   
caching to ./sy20/SDSSspec/0803/spSpec-52318-0803-550.fit8kb   
[=============                          ]  59.4kb / 182.8kb     
caching to ./sy20/SDSSspec/0831/spSpec-52294-0831-327.fitkb   
[=========                              ]  41.1kb / 182.8kb     
caching to ./sy20/SDSSspec/2018/spSpec-53800-2018-008.fit8kb   
[====================================   ]  164.5kb / 182.8kb    
caching to ./sy20/SDSSspec/2588/spSpec-54174-2588-614.fitkb    
[==============                         ]  64.0kb / 182.8kb     
caching to ./sy20/SDSSspec/1704/spSpec-53178-1704-496.fit
[==================                     ]  82.3kb / 182.8kb     
caching to ./sy20/SDSSspec/1338/spSpec-52765-1338-424.fit8kb   
[====================                   ]  91.4kb / 182.8kb     
caching to ./sy20/SDSSspec/2520/spSpec-5458